In [ ]:
!pip install asteroid
!pip install scaper
!pip install soxbindings
!pip install nussl

In [ ]:
from asteroid.losses import singlesrc_neg_sisdr as sdr

In [ ]:
a = torch.tensor(np.random.rand(10,10)).type(torch.float32)/1000
b = torch.tensor(np.random.rand(10,10)).type(torch.float32)/1000
sdr(a,b).sum()

tensor(800.)

In [ ]:
import torch

In [ ]:
import torch.nn.functional as F

In [ ]:
import numpy as np

In [ ]:
import torchaudio

In [ ]:
import librosa

In [ ]:
import numpy as np
import IPython.display as ipd

In [ ]:
import torch.nn as nn

In [ ]:
import torch.optim as optim

In [ ]:
from torch.nn import LayerNorm as LN

In [ ]:
import scaper
import nussl

SoX could not be found!

    If you do not have SoX, proceed here:
     - - - http://sox.sourceforge.net/ - - -

    If you do (or think that you should) have SoX, double-check your
    path variables.
    


In [ ]:
musdb = nussl.datasets.MUSDB18(folder = 'data1', download = True, subsets = ['train'])

Done!


In [ ]:
len(musdb.items)

94

In [ ]:
from pathlib import Path

# create foreground folder
fg_folder = Path('nussl/foreground').expanduser()  
fg_folder.mkdir(parents=True, exist_ok=True)                             

# create background folder - we need to provide one even if we don't use it
bg_folder = Path('nussl/background').expanduser()
bg_folder.mkdir(parents=True, exist_ok=True)

In [ ]:
for item in musdb:
    song_name = item['mix'].file_name
    for key, val in item['sources'].items():
        src_path = fg_folder / key 
        src_path.mkdir(exist_ok=True)
        src_path = str(src_path / song_name) + '.wav'
        val.write_audio_to_file(src_path)

In [ ]:
import warnings
warnings.filterwarnings('ignore')

In [ ]:
seed = 130

sc = scaper.Scaper(
    duration=1.0,
    fg_path=str(fg_folder),
    bg_path=str(bg_folder),
    random_state=seed
)

sc.sr = 44100
sc.n_channels = 1
sc.ref_db = -20

In [ ]:
sc.reset_fg_event_spec()

In [ ]:
sc.reset_fg_event_spec()
labels = ['vocals', 'drums', 'bass', 'other']

for label in labels:
    sc.add_event(label=('const', label),                # set the label value explicitly using a constant
                 source_file=('choose', []),            # choose the source file randomly from all files in the folder
                 source_time=('uniform', 0, 7),         # sample the source (stem) audio starting at a time between 0-7
                 event_time=('const', 0),               # always add the stem at time 0 in the mixture
                 event_duration=('const', sc.duration), # set the stem duration to match the mixture duration
                 snr=('uniform', 3, 4),                # choose an SNR for the stem uniformly between -5 and 5 dB
                 pitch_shift=('uniform', -2, 2),        # apply a random pitch shift between -2 and 2 semitones
                 time_stretch=('uniform', 0.8, 1.2))    # apply a random time stretch between 0.8 (faster) and 1.2 (slower)

In [ ]:
mixture_audio, mixture_jam, annotation_list, stem_audio_list = sc.generate(fix_clipping = True)

In [ ]:
len(stem_audio_list)

4

In [ ]:
ipd.display(ipd.Audio(data = mixture_audio.T, rate = 44100))
ipd.display(ipd.Audio(data = stem_audio_list[0].T, rate = 44100))
ipd.display(ipd.Audio(data = stem_audio_list[1].T, rate = 44100))
ipd.display(ipd.Audio(data = stem_audio_list[2].T, rate = 44100))
ipd.display(ipd.Audio(data = stem_audio_list[3].T, rate = 44100))

In [ ]:
dataset = []
for i in range(700):
  mixture_audio, mixture_jam, annotation_list, stem_audio_list = sc.generate(fix_clipping = True)
  dataset.append([mixture_audio] + stem_audio_list)

In [ ]:
try_set = []
sc.reset_fg_event_spec()
for i in range(400):
  event_parameters = {
    'label': ('const', 'vocals'),              
    'source_file': ('choose', []),             
    'source_time': ('uniform', 0, 7),
    'event_time': ('const', 0),
    'event_duration': ('const', sc.duration),
    'snr': ('uniform', -5, 5),
    'pitch_shift': ('uniform', -2, 2),
    'time_stretch': ('uniform', 0.8, 1.2)
  }
  sc.add_event(**event_parameters)
  
  event = sc._instantiate_event(sc.fg_spec[0])
  sc.reset_fg_event_spec()
  
  event_parameters['source_time'] = ('const', event.source_time)
  event_parameters['pitch_shift'] = ('const', event.pitch_shift)
  event_parameters['time_stretch'] = ('const', event.time_stretch)
  labels = ['vocals', 'drums', 'bass', 'other']
  for label in labels:
    event_parameters['label'] = ('const', label)
    coherent_source_file = event.source_file.replace('vocals', label)
    event_parameters['source_file'] = ('const', coherent_source_file)
    sc.add_event(**event_parameters)
  mixture_audio, mixture_jam, annotation_list, stem_audio_list = sc.generate(fix_clipping=True)
  dataset.append([mixture_audio] + stem_audio_list)

  sc.reset_fg_event_spec()

In [ ]:
print(type(try_set[0][0]))
'''play(42100, try_set[0][0])
play(42100, try_set[0][1])
play(42100, try_set[0][2])'''

<class 'numpy.ndarray'>


'play(42100, try_set[0][0])\nplay(42100, try_set[0][1])\nplay(42100, try_set[0][2])'

In [ ]:
ipd.display(ipd.Audio(data = dataset[800][0].T, rate = 44100))
ipd.display(ipd.Audio(data = dataset[800][1].T, rate = 44100))

In [ ]:
musdb[0]['sources']['bass'].audio_data.shape, musdb[1]['mix'].audio_data.shape

((2, 300032), (2, 300032))

In [ ]:
musdb[0]['mix'].sample_rate

44100

In [ ]:
torch.cuda.get_device_name(0)

'Tesla T4'

In [ ]:
def play(sr, data):
    ipd.display(ipd.Audio(data = data, rate = sr))

In [ ]:
play(44100, data = musdb[0]['sources']['bass'].audio_data[0])
play(44100, data = musdb[0]['sources']['bass'].audio_data[1])

In [ ]:
musdb[0]['mix'].audio_data[1] + musdb[0]['mix'].audio_data[0] == musdb[0]['mix'].audio_data

In [ ]:
dataset1 = np.array(dataset)
dataset1.shape

(1100, 5, 44100, 1)

In [ ]:
dataset1 = dataset1.reshape((1100, 5, 44100))
dataset1.shape

(1100, 5, 44100)

In [ ]:
coh_set1 = np.array(coh_set)
coh_set1 = coh_set1.reshape((600, 2, 88200))
coh_set1.shape

(600, 2, 88200)

In [ ]:
play(44100, data = dataset1[291][0])
play(44100, data = dataset1[291][1])

In [ ]:
np.random.shuffle(dataset1)

# Network

In [ ]:
def make_input(arr):
  arr = arr[:, :, :44100-81]
  inp = torch.tensor(arr[:, 0, :])
  tar_voc = torch.tensor(arr[:, 1, :])
  tar_drums = torch.tensor(arr[:, 2, :])
  tar_bass = torch.tensor(arr[:, 3, :])
  tar_others = torch.tensor(arr[:, 4, :])
  return inp, tar_voc, tar_drums, tar_bass, tar_others

In [ ]:
a, b, c, d, e = make_input(dataset1[0:2])
a.shape, b.shape, c.shape, d.shape, e.shape

(torch.Size([2, 44019]),
 torch.Size([2, 44019]),
 torch.Size([2, 44019]),
 torch.Size([2, 44019]),
 torch.Size([2, 44019]))

In [ ]:
44100//201, 201 - 44100%201, 44100%201, (44100-81)/201, 219*201 + 81

(219, 120, 81, 219.0, 44100)

In [ ]:
pyt
class net(nn.Module):
    def __init__(self, device = 'cpu'):
        super().__init__()
        self.device = device
        
        #encoder
        self.enc_lnin = LN([1, 201], elementwise_affine=False)
        self.enc_conv0 = nn.Conv1d(in_channels = 1, out_channels = 62, kernel_size = 6, stride = 3)
        self.prelu0 = nn.PReLU(); self.enc_ln0 = LN([62, 66])
        self.enc_conv1 = nn.Conv1d(in_channels = 62, out_channels = 125, kernel_size = 6, stride = 3)
        self.prelu1 = nn.PReLU(); self.enc_ln1 = LN([125, 21])
        self.enc_conv2 = nn.Conv1d(125, 250, 6, 3); self.prelu2 = nn.PReLU(); self.enc_ln2 = LN([250, 6])
        self.enc_conv3a = nn.Conv1d(250, 500, 6, 1);
        self.enc_conv3b = nn.Conv1d(250, 500, 6, 1);
        self.normalize = nn.GroupNorm(1, 500)

        #LSTM
        self.lstm1 = nn.LSTM(1500, 1500, 2, batch_first = True, bidirectional = True)
        self.lstm2 = nn.LSTM(1500, 1500, 2, batch_first = True, bidirectional = True)
        self.fc1 = nn.Linear(3000, 2200); self.fc1_prelu = nn.PReLU(); self.fc1_ln = LN([2200])
        self.fc2 = nn.Linear(2200, 1500); self.fc2_ln = LN([1500])
    

        #decoder
        self.deconv3 = nn.ConvTranspose1d(500, 250, 6, 1); self.deprelu3 = nn.PReLU()
        self.ln_d3 = LN([250, 6])
        self.deconv2 = nn.ConvTranspose1d(500, 125, 6, 3); self.deprelu2 = nn.PReLU()
        self.ln_d2 = LN([125, 21])
        self.deconv1 = nn.ConvTranspose1d(250, 62, 6, 3); self.deprelu1 = nn.PReLU()
        self.ln_d1 = LN([62, 66])
        self.deconv0 = nn.ConvTranspose1d(62, 1, 6, 3); self.deprelu0 = nn.PReLU()
        self.ln_d0 = LN([1, 201], elementwise_affine=False)
        self.weight_flag = 0
        self.masks_flag = 0
        
        self.deconv3b = nn.ConvTranspose1d(500, 250, 6, 1); self.deprelu3b = nn.PReLU()
        self.ln_d3b = LN([250, 6])
        self.deconv2b = nn.ConvTranspose1d(500, 125, 6, 3); self.deprelu2b = nn.PReLU()
        self.ln_d2b = LN([125, 21])
        self.deconv1b = nn.ConvTranspose1d(250, 62, 6, 3); self.deprelu1b = nn.PReLU()
        self.ln_d1b = LN([62, 66])
        self.deconv0b = nn.ConvTranspose1d(62, 1, 6, 3); self.deprelu0b = nn.PReLU()
        self.ln_d0b = LN([1, 201], elementwise_affine=False)
        
        self.deconv3l = nn.ConvTranspose1d(500, 250, 6, 1); self.deprelu3l = nn.PReLU()
        self.ln_d3l = LN([250, 6])
        self.deconv2l = nn.ConvTranspose1d(500, 125, 6, 3); self.deprelu2l = nn.PReLU()
        self.ln_d2l = LN([125, 21])
        self.deconv1l = nn.ConvTranspose1d(250, 62, 6, 3); self.deprelu1l = nn.PReLU()
        self.ln_d1l = LN([62, 66])
        self.deconv0l = nn.ConvTranspose1d(62, 1, 6, 3); self.deprelu0l = nn.PReLU()
        self.ln_d0l = LN([1, 201], elementwise_affine=False)

    def forward(self, x, bt, seqlen):
        #encoder
        x0 = self.enc_ln0(self.prelu0(self.enc_conv0(self.enc_lnin(x))))
        x1 = self.enc_ln1(self.prelu1(self.enc_conv1(x0)))
        x2 = self.enc_ln2(self.prelu2(self.enc_conv2(x1)))
        x_r = F.relu(self.enc_conv3a(x2))
        x_g = F.sigmoid(self.enc_conv3b(x2))
        x_wt = x_r*x_g
        
        x_b = self.normalize(x_wt)
        x_b = torch.reshape(x_b, (bt, seqlen, 500))
        x_bb = torch.cat((torch.zeros((bt, 1, 500)).type(torch.float32).to(self.device), x_b[:, :seqlen-1, :]), 1)
        x_ba = torch.cat((x_b[:, 1:, :], torch.zeros((bt, 1, 500)).type(torch.float32).to(self.device)), 1)
        
        x_lstm = torch.cat((x_bb, x_b, x_ba), 2)
        
        if self.weight_flag == 1:
            return x_wt
        
        #LSTM
        x_lstm, (h, c) = self.lstm1(x_lstm)
        x1_lstm, (h, c) = self.lstm2((x_lstm[:, :, :1500] + x_lstm[:, :, 1500:])/2)
        x1_lstm = x_lstm + x1_lstm
        x1_lstm = x1_lstm.reshape(bt*seqlen, 3000)
        x1_lstm = self.fc1_ln(self.fc1_prelu(self.fc1(x1_lstm)))
        x1_lstm = (F.tanh(self.fc2_ln(self.fc2(x1_lstm)))+1)/2
        x_m1 = x1_lstm[:, :500]
        x_m2 = x1_lstm[:, 500:1000]
        x_m3 = x1_lstm[:, 1000:]
        x_m1 = torch.reshape(x_m1, (bt*seqlen, 500, 1))
        x_m2 = torch.reshape(x_m2, (bt*seqlen, 500, 1))
        x_m3 = torch.reshape(x_m3, (bt*seqlen, 500, 1))
        if self.masks_flag == 1:
            return x_m1, x_m2, x_m3
        x_m1 = x_m1*x_wt
        x_m2 = x_m2*x_wt
        x_m3 = x_m3*x_wt
        
        #decoder
        x_voc = torch.cat((self.ln_d3(self.deprelu3(self.deconv3(x_m1))), x2), 1)
        x_voc = torch.cat((self.ln_d2(self.deprelu2(self.deconv2(x_voc))), x1), 1)
        x_voc = self.ln_d1(self.deprelu1(self.deconv1(x_voc)))
        x_voc = torch.tanh(self.ln_d0(self.deprelu0(self.deconv0(x_voc))))
        x_voc = torch.reshape(x_voc, (bt, seqlen*201))
        
        x_drm = torch.cat((self.ln_d3b(self.deprelu3b(self.deconv3b(x_m2))), x2), 1)
        x_drm = torch.cat((self.ln_d2b(self.deprelu2b(self.deconv2b(x_drm))), x1), 1)
        x_drm = self.ln_d1b(self.deprelu1b(self.deconv1b(x_drm)))
        x_drm = torch.tanh(self.ln_d0b(self.deprelu0b(self.deconv0b(x_drm))))
        x_drm = torch.reshape(x_drm, (bt, seqlen*201))

        x_bas = torch.cat((self.ln_d3l(self.deprelu3l(self.deconv3l(x_m3))), x2), 1)
        x_bas = torch.cat((self.ln_d2l(self.deprelu2l(self.deconv2l(x_bas))), x1), 1)
        x_bas = self.ln_d1l(self.deprelu1l(self.deconv1l(x_bas)))
        x_bas = torch.tanh(self.ln_d0l(self.deprelu0l(self.deconv0l(x_bas))))
        x_bas = torch.reshape(x_bas, (bt, seqlen*201))

        return x_voc, x_drm, x_bas

In [ ]:
trial_net = net()
aud, tar_voc, tar_drm, tar_bas, tar_oth = make_input(dataset1[0:5])
#aud = torch.tensor(aud, dtype=torch.float32)
#print(trial_net(aud, 2, 2)[0])# trial_net(aud, 2, 2)[1]
a, b, c = trial_net(aud.type(torch.float32).reshape((5*219, 1, 201)), 5, 219)
a.shape, b.shape, c.shape

(torch.Size([5, 44019]), torch.Size([5, 44019]), torch.Size([5, 44019]))

In [ ]:
separator = net('cuda:0').cuda()

In [ ]:
separator.load_state_dict(torch.load('separator1.pt'))

In [ ]:
torch.cuda.empty_cache()

In [ ]:
optimizer = optim.Adagrad(separator.parameters(), lr = 0.04)

In [ ]:
for g in optimizer.param_groups:
    g['lr'] = 0.01

In [ ]:
separator.train()
epochs = 1
for i in range(1, epochs+1):
    bt = 10
    seqlen = 219
    np.random.shuffle(dataset1)

    for j in range(1100//bt):
        inp, tar_voc, tar_drm, tar_bas, tar_oth = make_input(dataset1[j*bt : (j+1)*bt])
        est_voc, est_drm, est_bas = separator(inp.reshape((bt * 219, 1, 201)).type(torch.float32).cuda(), bt, seqlen)

        loss = 0
        est_voc = (est_voc - est_voc.mean(dim = 1, keepdim = True))/est_voc.norm(dim = 1, keepdim = True)*200
        tar_voc = (tar_voc - tar_voc.mean(dim = 1, keepdim = True)).cuda()
        tar_voc = (tar_voc/tar_voc.norm(dim = 1, keepdim = True)*200).type(torch.float32)
        est_drm = est_drm - est_drm.mean(dim = 1, keepdim = True)
        est_drm = (est_drm/est_drm.norm(dim = 1, keepdim = True)*200).type(torch.float32)
        tar_drm = (tar_drm - tar_drm.mean(dim = 1, keepdim = True)).cuda()
        tar_drm = (tar_drm/tar_drm.norm(dim = 1, keepdim = True)*200).type(torch.float32)
        est_bas = est_bas - est_bas.mean(dim = 1, keepdim = True)
        est_bas = (est_bas/est_bas.norm(dim = 1, keepdim = True)*200).type(torch.float32)
        tar_bas = (tar_bas - tar_bas.mean(dim = 1, keepdim = True)).cuda()
        tar_bas = (tar_bas/tar_bas.norm(dim = 1, keepdim = True)*200).type(torch.float32)
        inp = (inp - inp.mean(dim = 1, keepdim = True)).cuda()
        inp = (inp/inp.norm(dim = 1, keepdim = True)*800).type(torch.float32)
        tar_oth = (tar_oth - tar_oth.mean(dim = 1, keepdim = True)).cuda()
        tar_oth = (tar_oth/tar_oth.norm(dim = 1, keepdim = True)*200).type(torch.float32)

        #loss += sdr(est_voc, tar_voc).sum()/bt + sdr(est_bas, tar_bas).sum()/bt + sdr(est_drm, tar_drm).sum()/bt + sdr(inp - (est_drm + est_bas + est_voc), tar_oth).sum()/bt
        loss = 15*F.l1_loss(tar_voc, est_voc) + 5*F.l1_loss(tar_drm, est_drm) + 5*F.l1_loss(tar_bas, est_bas) + F.l1_loss(inp - est_voc - est_drm - est_bas, tar_oth)


        print("Loss(ep-{} bt-{}) : {}".format(i, j, loss))
        print(loss.data.dtype)
        loss.backward()
        #print(separator.enc_conv1.weight.grad)
        #print(separator.enc_conv6.weight.grad)
        #print(separator.deconv6a.weight.grad)
        torch.nn.utils.clip_grad_norm_(separator.parameters(), 3)
        optimizer.step()
        optimizer.zero_grad()
        
        del tar_bas
        del tar_oth
        del tar_voc
        del tar_drm
        del inp
        del est_bas
        del est_drm
        del est_voc
        torch.cuda.empty_cache()

Loss(ep-1 bt-0) : 18.576955795288086
torch.float32
Loss(ep-1 bt-1) : 18.177736282348633
torch.float32
Loss(ep-1 bt-2) : 17.138547897338867
torch.float32
Loss(ep-1 bt-3) : 18.55108070373535
torch.float32
Loss(ep-1 bt-4) : 18.078996658325195
torch.float32
Loss(ep-1 bt-5) : 17.400941848754883
torch.float32
Loss(ep-1 bt-6) : 17.912052154541016
torch.float32
Loss(ep-1 bt-7) : 17.94159698486328
torch.float32
Loss(ep-1 bt-8) : 18.923429489135742
torch.float32
Loss(ep-1 bt-9) : 17.780054092407227
torch.float32
Loss(ep-1 bt-10) : 18.34862518310547
torch.float32
Loss(ep-1 bt-11) : 18.379913330078125
torch.float32
Loss(ep-1 bt-12) : 16.97247314453125
torch.float32
Loss(ep-1 bt-13) : 18.468460083007812
torch.float32
Loss(ep-1 bt-14) : 18.29515838623047
torch.float32
Loss(ep-1 bt-15) : 17.829389572143555
torch.float32
Loss(ep-1 bt-16) : 18.226118087768555
torch.float32
Loss(ep-1 bt-17) : 17.414350509643555
torch.float32
Loss(ep-1 bt-18) : 18.505186080932617
torch.float32
Loss(ep-1 bt-19) : 18.61319

In [ ]:
test_set = []
sc.reset_fg_event_spec()
for i in range(5):
  event_parameters = {
    'label': ('const', 'vocals'),              
    'source_file': ('choose', []),             
    'source_time': ('uniform', 0, 7),
    'event_time': ('const', 0),
    'event_duration': ('const', sc.duration),
    'snr': ('uniform', 3, 4),
    'pitch_shift': ('uniform', -2, 2),
    'time_stretch': ('uniform', 0.8, 1.2)
  }
  sc.add_event(**event_parameters)
  
  event = sc._instantiate_event(sc.fg_spec[0])
  sc.reset_fg_event_spec()
  
  event_parameters['source_time'] = ('const', event.source_time)
  event_parameters['pitch_shift'] = ('const', event.pitch_shift)
  event_parameters['time_stretch'] = ('const', event.time_stretch)
  labels = ['vocals', 'drums', 'bass', 'other']
  for label in labels:
    event_parameters['label'] = ('const', label)
    coherent_source_file = event.source_file.replace('vocals', label)
    event_parameters['source_file'] = ('const', coherent_source_file)
    sc.add_event(**event_parameters)
  mixture_audio, mixture_jam, annotation_list, stem_audio_list = sc.generate(fix_clipping=True)
  test_set.append([mixture_audio] + stem_audio_list)

  sc.reset_fg_event_spec()

In [ ]:
test_set1 = np.array(test_set)
test_set1 = test_set1.reshape((5, 5, 44100))
test_set1.shape

(5, 5, 44100)

In [ ]:
ipd.display(ipd.Audio(data = test_set1[0][0], rate = 44100))
ipd.display(ipd.Audio(data = test_set1[0][1], rate = 44100))
ipd.display(ipd.Audio(data = test_set1[0][2], rate = 44100))
ipd.display(ipd.Audio(data = test_set1[0][3], rate = 44100))
ipd.display(ipd.Audio(data = test_set1[0][4], rate = 44100))

In [ ]:
bt = 3
seqlen = 219

separator.eval()
separator.masks_flag = 0

inp, tar_voc, tar_drm, tar_bas, tar_oth = make_input(test_set1[0 : 3])
est_voc, est_drm, est_bas = separator(inp.reshape((bt * 219, 1, 201)).type(torch.float32).cuda(), bt, seqlen)

torch.cuda.empty_cache()

play(42100, data = inp[0])
play(42100, data = tar_voc[0].detach().numpy())
play(42100, data = est_voc[0].detach().cpu().numpy())
play(42100, data = tar_drm[0].detach().numpy())
play(42100, data = est_drm[0].detach().cpu().numpy())
play(42100, data = tar_bas[0].detach().numpy())
play(42100, data = est_bas[0].detach().cpu().numpy())

del est_drm
del est_bas
del est_voc
torch.cuda.empty_cache()

# 

In [ ]:
torch.save(separator.state_dict(), 'separator-698Rproject-SSfin-l1-2.pt')

In [ ]:
a = torch.tensor(np.array([1,1,1]), dtype = torch.float64)
a.type(torch.float32).dtype

torch.float32

In [ ]:
a

tensor([[[2, 3]],

        [[3, 4]]])

In [ ]:
a = np.array([[a,a]])
a.shape

(1, 2, 4)

In [ ]:
a

array([[[2, 3, 3, 4],
        [2, 3, 3, 4]]])

In [ ]:
a = 'nan'

In [ ]:
a = nan

NameError: ignored

In [ ]:
import torch
torch.isnan(1)

TypeError: ignored

In [ ]:
a = np.array([[[1,2,1],[2,3,4],[1,2,1],[2,3,4]],[[1,2,1],[2,3,4],[1,2,1],[2,3,4]],[[1,2,1],[2,3,4],[1,2,1],[2,3,4]]])
a.shape
b = a.copy() + 1
c = a.copy() + 2

In [ ]:
a = torch.tensor(a)
b = torch.tensor(b)
c = torch.tensor(c)

In [ ]:
torch.cat((a,b), 0)

tensor([[[1, 2, 1],
         [2, 3, 4],
         [1, 2, 1],
         [2, 3, 4]],

        [[1, 2, 1],
         [2, 3, 4],
         [1, 2, 1],
         [2, 3, 4]],

        [[1, 2, 1],
         [2, 3, 4],
         [1, 2, 1],
         [2, 3, 4]],

        [[2, 3, 2],
         [3, 4, 5],
         [2, 3, 2],
         [3, 4, 5]],

        [[2, 3, 2],
         [3, 4, 5],
         [2, 3, 2],
         [3, 4, 5]],

        [[2, 3, 2],
         [3, 4, 5],
         [2, 3, 2],
         [3, 4, 5]]], dtype=torch.int32)

In [ ]:
a.shape

torch.Size([3, 4, 3])

In [ ]:
torch.cat((a,a,a), 2)

tensor([[[1, 2, 1, 1, 2, 1, 1, 2, 1],
         [2, 3, 4, 2, 3, 4, 2, 3, 4],
         [1, 2, 1, 1, 2, 1, 1, 2, 1],
         [2, 3, 4, 2, 3, 4, 2, 3, 4]],

        [[1, 2, 1, 1, 2, 1, 1, 2, 1],
         [2, 3, 4, 2, 3, 4, 2, 3, 4],
         [1, 2, 1, 1, 2, 1, 1, 2, 1],
         [2, 3, 4, 2, 3, 4, 2, 3, 4]],

        [[1, 2, 1, 1, 2, 1, 1, 2, 1],
         [2, 3, 4, 2, 3, 4, 2, 3, 4],
         [1, 2, 1, 1, 2, 1, 1, 2, 1],
         [2, 3, 4, 2, 3, 4, 2, 3, 4]]], dtype=torch.int32)

In [ ]:
k = torch.cat((torch.zeros((3, 1, 3)), a[:, 1:, :]), 1)

In [ ]:
k.shape

torch.Size([3, 4, 3])

In [ ]:
d = torch.tensor(np.array([[[0,2],[2,3]], [[2,2],[2,2]]]))
d.shape

torch.Size([2, 2, 2])

In [ ]:
a = LN([2], elementwise_affine=False)
tr = nn.Sequential(a)
a.weight

In [ ]:
F.tanh(d)

C:\Users\saias\anaconda3\envs\pytor\lib\site-packages\torch\nn\functional.py:1794: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")


tensor([[[0.0000, 0.9640],
         [0.9640, 0.9951]],

        [[0.9640, 0.9640],
         [0.9640, 0.9640]]])